In [4]:
import json
import pandas as pd
import numpy as np
from haversine import haversine, Unit
import datetime
from statistics import stdev
import plotly.graph_objects as go
from plotly.subplots import make_subplots


#User Defined Variables
circuitName = "cartagena"
finishLineMeters = 5
frontSuspensionLogName = 'Fork      '
rearSuspensionLogName = 'Shock'

#Read Log file
log = pd.read_csv("exportedLog.csv", delimiter=';')

#Import Circuits
with open("../circuits.json") as f:
    circuits = json.load(f)

finishLineLat = circuits.get(circuitName).get('FinishLine').get('latitude')
finishLineLong = circuits.get(circuitName).get('FinishLine').get('longitude')

#Remove i2m metaData Unwanted Lines
log.drop(log.index[0], inplace=True)
log.drop(log.index[0], inplace=True)
log.drop(log.index[0], inplace=True)
del log[log.columns[0]]

log = log.apply(pd.to_numeric)

time = log['Time [s]']
lat = log['LAT [Degrees]']
long = log['LONG [Degrees]']

def isNearFinishLine(currentLat, currentLong):
    finishline = (finishLineLat, finishLineLong)
    currentLocation = (currentLat, currentLong)
    if haversine(finishline, currentLocation, unit='m') < finishLineMeters:
        return True
    return False

#Detecting each new lap, comparing lap times & logging the fastest lap with it's start and end locations
previousLapTime = 0
previousLapLocation = 0
fastestLapStart = 0
fastestLapEnd = 0
lapsCompleted = 0
fastestLap = 0
for x in range(0, len(time)):
    if ~np.isnan(lat.iloc[x]) and ~np.isnan(lat.iloc[x]) and isNearFinishLine(lat.iloc[x], long.iloc[x]):
        lapTime = time.iloc[x] - previousLapTime
        previousLapTime = time.iloc[x]
        lapsCompleted = lapsCompleted + 1
        if fastestLap == 0:
            fastestLap = lapTime
            fastestLapEnd = x
        elif lapTime < fastestLap:
            fastestLap = lapTime
            fastestLapStart = previousLapLocation
            fastestLapEnd = x
        previousLapLocation = x
        print("Lap", lapsCompleted, str(datetime.timedelta(seconds=lapTime)))

print("Your fastest lap was", str(datetime.timedelta(seconds=fastestLap)))

#Removing everything but the fastest Lap
indexesBeforeFastest = []
indexesAfterFastest = []

for x in range(0, fastestLapStart):
    indexesBeforeFastest.append(x+3)  #Need the +3 because 3 indexes are removed at the start

for x in range(fastestLapEnd, len(log)):
    indexesAfterFastest.append(x)

log.drop(indexesAfterFastest, inplace=True)
log.drop(indexesBeforeFastest, inplace=True)

#Remove lines with NaN's
log = log.dropna(subset=[frontSuspensionLogName])
log = log.dropna(subset=[rearSuspensionLogName])


time = log['Time [s]']
frontSuspension = log[frontSuspensionLogName]
rearSuspension = log[rearSuspensionLogName]
frontSuspensionSpeedList = []
rearSuspensionSpeedList = []

#create suspension speed array's
for x in range(0, len(time)):
    timeDif = (time.iloc[x] - time.iloc[x-1])
    frontSusDiff = (frontSuspension.iloc[x] - frontSuspension.iloc[x-1]) 
    rearSusDiff = (rearSuspension.iloc[x] - rearSuspension.iloc[x-1]) 
    frontSpeedCalc = frontSusDiff / timeDif
    rearSpeedCalc = rearSusDiff / timeDif

    #Needed because i2m logger sends some crazy numbers when it's switching off
    if frontSpeedCalc > -1000 and frontSpeedCalc < 1000 :
        frontSuspensionSpeedList.append(frontSpeedCalc)
    if rearSpeedCalc > -1000 and rearSpeedCalc < 1000 :
        rearSuspensionSpeedList.append(rearSpeedCalc)

fig = make_subplots(
    rows = 2, cols = 2)

frontSusTrace = go.Histogram(x = frontSuspensionSpeedList, name='Front Suspension Histogram',
                             xbins=dict(
                                 start=-700,
                                 end=700,
                                 size=20
                             ))
rearSusTrace = go.Histogram(x = rearSuspensionSpeedList, name = 'Rear Suspension Histogram',
                             xbins=dict(
                                 start=-200,
                                 end=200,
                                 size=10
                             ))
frontSpeedTrace = go.Scatter(x = time, y = frontSuspensionSpeedList, name='Front Suspension Speed', mode='lines')
rearSpeedTrace = go.Scatter(x = time, y = rearSuspensionSpeedList, name='Rear Suspension Speed', mode='lines')

fig.append_trace(frontSusTrace, 1, 1)
fig.append_trace(rearSusTrace, 2, 1)
fig.append_trace(frontSpeedTrace, 1, 2)
fig.append_trace(rearSpeedTrace, 2, 2)

#add slow speed to front sus
fig.add_vrect(
    x0="-100", x1="100",row=1, col=1,
    annotation_text="Slow Speed", annotation_position="top left",
    fillcolor="LightSalmon", opacity=0.5,
    layer="below", line_width=0,
),

#add slow speed to rear sus
fig.add_vrect(
    x0="-20", x1="20",row=2, col=1,
    annotation_text="Slow Speed", annotation_position="top left",
    fillcolor="LightSalmon", opacity=0.5,
    layer="below", line_width=0,
),

fig.add_hline(
    y=400,row=1, col=2,
    annotation_text="Compression Limit", annotation_position="top left"
),

fig.add_hline(
    y=-400,row=1, col=2,
    annotation_text="Rebound Limit", annotation_position="top left"
),

fig.update_layout(title='Suspension Histograms With Table', autosize=True)

figTable = go.Figure(data=[
    go.Table(header = dict(values=['Front Delta Max', 'Front Standard Deviation','Rear Delta Max', 'Rear Standard Deviation']),
            cells = dict(values=[[max(frontSuspensionSpeedList)],[stdev(frontSuspensionSpeedList)],[max(rearSuspensionSpeedList)],[stdev(rearSuspensionSpeedList)]]))
])

fig.show()
figTable.show()


C:\Users\marti\AppData\Local\Temp\ipykernel_34228\3695751747.py:18: DtypeWarning:

Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.



Lap 1 0:01:43.900000
Lap 2 0:01:38.500000
Lap 3 0:01:37.600000
Lap 4 0:01:37.600000
Your fastest lap was 0:01:37.600000
